In [0]:
from pyspark.sql.types import *
import pyspark
from pyspark.sql import SparkSession
import pandas as pd
import sparknlp
from pyspark.sql.functions import col, udf, regexp_extract, explode, lower, length, trim, when, regexp_replace
from pyspark.sql import functions as F
import re
import numpy as np

# Embedded Requirements Vectors
Using pretrained models- get requirements embeddings

In [0]:
spark = sparknlp.start()
requirements_embed_pd = pd.read_csv('data/indeed_requirements.csv')

In [0]:
pip install sentence-transformers

In [0]:
from sentence_transformers import SentenceTransformer
model1 = SentenceTransformer('all-MiniLM-L6-v2')
model2 = SentenceTransformer('all-MPNet-base-v2')

In [0]:
# Generate embeddings (normalized)
requirements_embed_pd['Embeddings_Model1'] = requirements_embed_pd['Requirements_Text'].apply(lambda x: model1.encode(x) if x else None)
requirements_embed_pd['Embeddings_Model2'] = requirements_embed_pd['Requirements_Text'].apply(lambda x: model2.encode(x) if x else None)

# Clustering of Embedded Requirements
Each cluster represents a job category (e.g 'Data Scientist - Business')

In [0]:
from pyspark.ml.evaluation import ClusteringEvaluator
from pyspark.ml.clustering import KMeans
from pyspark.ml.feature import VectorAssembler, PCA
from pyspark.ml.linalg import Vectors
from pyspark.ml.functions import array_to_vector
from sklearn.cluster import DBSCAN
import matplotlib.pyplot as plt

In [0]:
spark = sparknlp.start()
requirements_embed_pd = pd.read_csv('data/indeed_embeddings.csv')
requirements_embed_spark = spark.createDataFrame(requirements_embed_pd)

In [0]:
# UDF to convert string to array of floats
def string_to_array(embedding_str):
    return [float(x) for x in embedding_str.strip("[]").split(",")]

string_to_array_udf = udf(string_to_array, ArrayType(FloatType()))
requirements_embed_spark = requirements_embed_spark.withColumn(
    "Embeddings_Model1", string_to_array_udf(col("Embeddings_Model1"))
).withColumn(
    "Embeddings_Model2", string_to_array_udf(col("Embeddings_Model2"))
)

In [0]:
requirements_embed_spark = requirements_embed_spark.withColumn("Embeddings_Model1_Vector", array_to_vector(col("Embeddings_Model1")))
requirements_embed_spark = requirements_embed_spark.withColumn("Embeddings_Model2_Vector", array_to_vector(col("Embeddings_Model2")))

# Ensure embeddings are in the correct vector format
vector_assembler1 = VectorAssembler(inputCols=["Embeddings_Model1_Vector"], outputCol="features_model1")
vector_assembler2 = VectorAssembler(inputCols=["Embeddings_Model2_Vector"], outputCol="features_model2")
requirements_embed_spark = vector_assembler1.transform(requirements_embed_spark)
requirements_embed_spark = vector_assembler2.transform(requirements_embed_spark)

## Chose number of clusters k

In [0]:
k_values = range(3, 30)
ssd1 = []
ssd2 = []
silhouette_scores1 = []
silhouette_scores2 = []

for k in k_values:
    kmeans_1 = KMeans(featuresCol="features_model1", k=k)
    model_1 = kmeans_1.fit(requirements_embed_spark)
    ssd1.append(model_1.summary.trainingCost)

    predictions1 = model_1.transform(requirements_embed_spark)
    evaluator1 = ClusteringEvaluator(featuresCol="features_model1", predictionCol="prediction", metricName="silhouette")
    silhouette_scores1.append(evaluator1.evaluate(predictions1))


    kmeans_2 = KMeans(featuresCol="features_model2", k=k)
    model_2 = kmeans_2.fit(requirements_embed_spark)
    ssd2.append(model_2.summary.trainingCost)

    predictions2 = model_2.transform(requirements_embed_spark)
    evaluator2 = ClusteringEvaluator(featuresCol="features_model2", predictionCol="prediction", metricName="silhouette")
    silhouette_scores2.append(evaluator2.evaluate(predictions2))


In [0]:
# Visualization for Elbow Method
plt.figure(figsize=(10, 6))
plt.plot(k_values, ssd1, marker='o', label="Model 1")
plt.plot(k_values, ssd2, marker='o', label="Model 2")
plt.title("Elbow Method for Optimal k - Both Models")
plt.xlabel("Number of Clusters (k)")
plt.ylabel("Sum of Squared Distances")
plt.legend()
plt.grid()
plt.show()

In [0]:
# Visualization for Silhouette scores
plt.figure(figsize=(10, 6))
plt.plot(k_values, silhouette_scores1, marker='o', label="Model 1")
plt.plot(k_values, silhouette_scores2, marker='o', label="Model 2")
plt.title("Silhouette Scores for Optimal k - Both Models")
plt.xlabel("Number of Clusters (k)")
plt.ylabel("Silhouette Score")
plt.legend()
plt.grid()
plt.show()

## Clustering embedded requirements

In [0]:
# Define and fit the KMeans model
kmeans1 = KMeans(featuresCol="features_model1", predictionCol="Cluster_spark_KMeans_1", k=25)
kmeans_model1 = kmeans1.fit(requirements_embed_spark)
requirements_clusters = kmeans_model1.transform(requirements_embed_spark)

kmeans2 = KMeans(featuresCol="features_model2", predictionCol="Cluster_spark_KMeans_2", k=25)
kmeans_model2 = kmeans2.fit(requirements_clusters)
requirements_clusters = kmeans_model2.transform(requirements_clusters)

# View cluster assignments
requirements_clusters.select("Title","Company", "Requirements_Text", "Cluster_spark_KMeans_1", "Cluster_spark_KMeans_2").limit(20).display()


Uploading artifacts:   0%|          | 0/4 [00:00<?, ?it/s]

Uploading artifacts:   0%|          | 0/4 [00:00<?, ?it/s]

Title Company Requirements_Text Cluster_spark_KMeans_1 Cluster_spark_KMeans_2 Data Analytics Apple +3 years of experience Ability to lead data investigations and analysis projects with ambiguous requirements Advanced statistic and modeling knowledge Experience visualizing and presenting analyses in tools like Jupyter and Tableau Experience programming in Python in a professional setting Familiarity with distributed computation, storage, and workflow management (e.g. Splunk, Spark, Kubernetes, Kafka, Hadoop, MapReduce, AirFlow etc.) Experience with relational databases and SQL Highly organized, creative, motivated, and passionate about achieving results Curious and have excellent analytical and problem solving skills Excellent written, verbal, and data communication skills Bachelor's or Master's degree in computer science. Preferred Qualifications Familiarity with distributed computation, storage, and workflow management (e.g. Splunk, Spark, Kubernetes, Kafka, Hadoop, MapReduce, AirFlow etc.) 17 23 Junior Backend Big Data Developer ThetaRay into actionable designs and tasks, development, UT, and production troubleshooting Requirements 1-2 years of experience of hands-on development experience Experience developing data-oriented products preferably using Python/Java Experience in data processing FW such as Spark, Pandas, Hadoop, Airflow Experience in Distributed Databases (Such as Elasticsearch, Mongo, Redis, etc) Experience with developing microservices-based architecture Experience working in container-based environments using tools such as K8s, helm Experience working as a software developer in an Agile environment Nice to have: Experience in machine learning FWs such as SKLearn, Tensorflow Experience with RedHat OpenShift Dev Environment knowledge: GIT, Jenkins, Docker 13 13 Data Annotator Prisma Photonics A Bachelor of Science degree or equivalent (STEM fields an advantage). Strong attention to detail and a commitment to maintaining high-quality annotation standards. Good written and verbal skills, with the ability to work effectively with a diverse group of individuals. Availability to work full time when needed. Nice-to-haves: Familiarity with data annotation processes, especially non-structured data (images, video, audio). Experience working with seismic data, heat maps, or spectrograms Familiarity with SQL and data visualization tools. Experience with coding languages, preferably MATLAB and Python. 16 16 Marketing Data Analyst Plarium B.A/BSc in a highly quantitative field such as mathematics industrial engineering economics statistics or equivalent academic knowledge At least 2 years of hands-on data analysis and story-telling experience Proven experience with measuring online success and identifying optimization opportunities Excellent understanding of online marketing metrics High proficiency in SQL with demonstrated experience in querying large complex datasets Strong Excel / Google Sheets skills Experience with data visualization tools such as Qlik Sense and Looker A solid grasp of statistical significance models and tools Desired Marketing metrics of user funnel, user acquisition KPI’s What we offer A Workplace Designed for Your Well-Being - Comfortable Environment: Ergonomic chairs and desks to support your health. Beautifully designed spaces that inspire creativity. - On-Site Amenities: Gym, yoga room, and music room for relaxation and rejuvenation. - Delicious Perks: 5-star breakfast to kickstart your day. Freshly made coffee, shakes, and afternoon salads by our in-house barista. - Health & Wellness: Full health insurance coverage for your peace of mind. - Growth Opportunities: Learning and training programs to enhance your personal and professional skills. - Vibrant Culture: Happy hours, team events, and plenty of opportunities to connect with colleagues. Join us and experience a workplace where your well-being, growth, and enjoyment come first! 0 8 Junior Data Analyst aiOla B.Sc in Industrial Engineering, Dat

In [0]:
requirements_pd = requirements_clusters.select("Title", "Company", "Full Job Description", "Search Word", "Description", "Description_English", "Requirements_Text", "Embeddings_Model1", "Embeddings_Model2", "Cluster_spark_KMeans_1", "Cluster_spark_KMeans_2").toPandas()

In [0]:
# Extract embeddings as a NumPy array
embeddings1 = np.array(requirements_pd['Embeddings_Model1'].tolist())
embeddings2 = np.array(requirements_pd['Embeddings_Model2'].tolist())

# Apply DBSCAN
dbscan = DBSCAN(eps=0.3, min_samples=2, metric='cosine')
cluster_labels1_dbscan = dbscan.fit_predict(embeddings1)
cluster_labels2_dbscan = dbscan.fit_predict(embeddings2)

# Add cluster labels to the DataFrame
requirements_pd['Cluster_DBSCAN_Model1'] = cluster_labels1_dbscan
requirements_pd['Cluster_DBSCAN_Model2'] = cluster_labels2_dbscan

display(requirements_pd)


Uploading artifacts:   0%|          | 0/9 [00:00<?, ?it/s]

Uploading artifacts:   0%|          | 0/9 [00:00<?, ?it/s]

Title Company Full Job Description Search Word Description Description_English Requirements_Text Embeddings_Model1 Embeddings_Model2 Cluster_spark_KMeans_1 Cluster_spark_KMeans_2 Cluster_DBSCAN_Model1 Cluster_DBSCAN_Model2 Data Analytics Apple Summary Posted: Nov 7, 2024 Role Number: 200577967 We're looking for an exceptional data analyst with a strong background in distributed data processing and a demonstrated ability to turn data into actionable insights. As a data analyst for our Storage Data Analytics team at Apple, you'll play a crucial role in developing the fastest and most efficient SSDs for our products, including the iPhone, iPad, Apple Watch, and new Apple Silicon Macs. If you're passionate about continuously improving the ways we use data to make Apple's products amazing, we want to hear from you! Description On the Storage Data Analytics team, we are responsible for performing ad hoc data analysis, development and maintenance of distributed data pipelines, as well as creation and support of analysis tools. Our team focuses on Apple’s storage solutions. It is small and nimble, able to quickly explore ideas and present them to the storage teams and to leadership. Minimum Qualifications +3 years of experience Ability to lead data investigations and analysis projects with ambiguous requirements Advanced statistic and modeling knowledge Experience visualizing and presenting analyses in tools like Jupyter and Tableau Experience programming in Python in a professional setting Familiarity with distributed computation, storage, and workflow management (e.g. Splunk, Spark, Kubernetes, Kafka, Hadoop, MapReduce, AirFlow etc.) Experience with relational databases and SQL Highly organized, creative, motivated, and passionate about achieving results Curious and have excellent analytical and problem solving skills Excellent written, verbal, and data communication skills Bachelor's or Master's degree in computer science. Preferred Qualifications Familiarity with distributed computation, storage, and workflow management (e.g. Splunk, Spark, Kubernetes, Kafka, Hadoop, MapReduce, AirFlow etc.) Opened URL: https://il.indeed.com/rc/clk?jk=0433bc7e45e694a3&bb=r6UIYw2mow7Pn8IzQwq2_7gXyX4L0a9oUPOLDIseoxAN8l0MRFFfCqpU6vSJRCmVlzxZCXcY6V-lzbB66NkEzDukGjQJgUJrBPff0HR1apFcJos6F0MbonwvLMjHhNz9&xkcb=SoDD67M33wH7H8WWaB0JbzkdCdPP&fccid=8e007f7a76f9cee5&vjs=3 data Summary Posted: Nov 7, 2024 Role Number: 200577967 We're looking for an exceptional data analyst with a strong background in distributed data processing and a demonstrated ability to turn data into actionable insights. As a data analyst for our Storage Data Analytics team at Apple, you'll play a crucial role in developing the fastest and most efficient SSDs for our products, including the iPhone, iPad, Apple Watch, and new Apple Silicon Macs. If you're passionate about continuously improving the ways we use data to make Apple's products amazing, we want to hear from you! Description On the Storage Data Analytics team, we are responsible for performing ad hoc data analysis, development and maintenance of distributed data pipelines, as well as creation and support of analysis tools. Our team focuses on Apple’s storage solutions. It is small and nimble, able to quickly explore ideas and present them to the storage teams and to leadership. Minimum Qualifications +3 years of experience Ability to lead data investigations and analysis projects with ambiguous requirements Advanced statistic and modeling knowledge Experience visualizing and presenting analyses in tools like Jupyter and Tableau Experience programming in Python in a professional setting Familiarity with distributed computation, storage, and workflow management (e.g. Splunk, Spark, Kubernetes, Kafka, Hadoop, MapReduce, AirFlow etc.) Experience with relational databases and SQL Highly organized, creative, motivated, and passionate about achieving results Curious and have excellent analytical and problem solving skills Excellent writ

In [0]:
# Evaluating Clustering Results:

from sklearn.metrics import silhouette_score, calinski_harabasz_score, davies_bouldin_score

# Function to calculate clustering metrics
def evaluate_clustering(embeddings, labels, model_name, algorithm_name):
    metrics = {}
    if len(set(labels)) > 1:  # Ensure there is more than 1 cluster
        metrics['Silhouette Score'] = silhouette_score(embeddings, labels, metric='cosine')
        metrics['Calinski-Harabasz Index'] = calinski_harabasz_score(embeddings, labels)
        metrics['Davies-Bouldin Index'] = davies_bouldin_score(embeddings, labels)
    else:
        metrics['Silhouette Score'] = np.nan
        metrics['Calinski-Harabasz Index'] = np.nan
        metrics['Davies-Bouldin Index'] = np.nan
    metrics['Model'] = model_name
    metrics['Algorithm'] = algorithm_name
    return metrics

# Evaluate KMeans clustering
kmeans_metrics_model1 = evaluate_clustering(embeddings1, requirements_pd['Cluster_spark_KMeans_1'], 'Model 1', 'KMeans')
kmeans_metrics_model2 = evaluate_clustering(embeddings2, requirements_pd['Cluster_spark_KMeans_2'], 'Model 2', 'KMeans')

# Evaluate DBSCAN clustering
dbscan_metrics_model1 = evaluate_clustering(embeddings1, requirements_pd['Cluster_DBSCAN_Model1'], 'Model 1', 'DBSCAN')
dbscan_metrics_model2 = evaluate_clustering(embeddings2, requirements_pd['Cluster_DBSCAN_Model2'], 'Model 2', 'DBSCAN')

# Combine all metrics into a DataFrame for comparison
comparison_df = pd.DataFrame([kmeans_metrics_model1, kmeans_metrics_model2, dbscan_metrics_model1, dbscan_metrics_model2])

# Display the comparison
comparison_df.display()


Silhouette Score Calinski-Harabasz Index Davies-Bouldin Index Model Algorithm 0.26248163 21.84754087156475 1.83935533066418 Model 1 KMeans 0.2827356 22.8958327876751 1.6672830889826642 Model 2 KMeans 0.51557064 19.793703701791966 1.008450139759225 Model 1 DBSCAN 0.27035204 12.199062563046002 1.0257032821412497 Model 2 DBSCAN

Silhouette Score: (Closer to 1 indicates better-defined clusters.)

3 > 2 > 4 > 1


Calinski-Harabasz Index: (Higher values indicate better cluster separation.)

2 > 1 > 3 > 4


Davies-Bouldin Index: (Lower values indicate better clustering quality.)

3 > 4 > 2 > 1

**Option 3 seems best.**